Вариант №4.

In [1]:
import numpy as np
import plotly as ply
import plotly.graph_objects as go
import plotly.express as px


In [18]:
#Функции начальных условий
def R0_1(x):
    return (-2*x**3 + 3*x**2 + 2*x +3)
def R0_2(x):
    return (2*x**3 - x**2 + 2*x -1)
def R0_3(x):
    return (-2*x**3 + x**2 + 6*x +1)

In [19]:
#Функция для нахождения точного решения
def r_th(a, x, t , R0):
    return (R0(x - a*t))

In [35]:
Tn = 100
Xm = 100
A = [-1, 2, -3]
R_th = [R0_1, R0_2, R0_3]
def R_prec(Tn, Xm, n):
    T = np.linspace(0, 1, Tn)
    X = np.linspace(0, 1, Xm)
    R = []
    #R = np.array([np.array([]), np.array([]), np.array([])])
    for t in T:
        R.append([])
        for x in X:
            R[-1].append(r_th(A[n], x, t , R_th[n]))

    return (X, T, R)
    

In [70]:
#Функция для нахождения приближенного решения по схеме бегущего счета(углок)
def corner (Tn, Xm, a, R0):
    R = np.zeros((Tn, Xm))
    X = np.linspace(0, 1, Xm)
    T = np.linspace(0, 1, Tn)
    tau = T[1] - T[0]
    h = X[1] - X[0]
    R[0, :] = R0(X)
    R[:, Xm-1] = R0(1 - a*T)
    R[:, 0] = R0(-a*T)
    if a > 0:
        #R[:, 0] = R0(-a*T)
        for n in range (Tn-1):
            for m in range(1, Xm):
                R[n+1, m] = (R[n, m] + (a*tau/h)*R[n+1, m-1])/(1 + a*tau/h)
    else:
        #R[:, Xm-1] = R0(1 - a*T)
        for n in range (Tn-1):
            for m in range(Xm - 2, -1, -1):
                R[n+1, m] = (R[n, m] - (a*tau/h)*R[n+1, m+1])/(1 - a*tau/h)
    return(X, T, R)
    

In [22]:
#Функция для построенния графика решения
def ploter(R_given, title):
    fig = go.Figure(go.Surface(
        contours = {
            "x": {"show": False, "start": 1.5, "end": 2, "size": 0.04, "color":"white"},
            "z": {"show": False, "start": 10, "end": 2, "size": 0.05}
        },
        x = R_given[0],
        y = R_given[1],
        z = R_given[2],
        opacity=0.4
    ))
    fig.update_layout(
        title=title,
        xaxis_title="x Axis Title",
        yaxis_title="T",
            scene = {
                "xaxis": {"nticks": 20},
                'zaxis': {"nticks": 20},
                "zaxis": {"nticks": 20},
                'camera_eye': {"x": 0.4, "y": -1.5, "z": 0.5},
                "aspectratio": {"x": 1, "y": 1, "z": 0.5}
            })
    fig.show()

In [23]:
# накладывает решения друг на друга
def merging_ploter(R_given, R_given1, title):
    fig = go.Figure(data = [
        go.Surface(
        contours = {
            "x": {"show": False, "start": 1.5, "end": 2, "size": 0.04, "color":"white"},
            "z": {"show": False, "start": 10, "end": 2, "size": 0.05}
        },
        x = R_given[0],
        y = R_given[1],
        z = R_given[2],
        opacity=1,
        colorscale = 'redor'
        ),
        go.Surface(contours = {
            "x": {"show": False, "start": 1.5, "end": 2, "size": 0.04, "color":"white"},
            "z": {"show": False, "start": 10, "end": 2, "size": 0.05}
        },
        x = R_given1[0],
        y = R_given1[1],
        z = R_given1[2],
        opacity=0.4,
        colorscale  = 'Blues')
                           ])
    fig.update_layout(title = title,
            scene = {
                "xaxis": {"nticks": 20},
                'zaxis': {"nticks": 20},
                "zaxis": {"nticks": 20},
                'camera_eye': {"x": 0.4, "y": -1.5, "z": 0.5},
                "aspectratio": {"x": 1, "y": 1, "z": 0.5}
            })
    fig.show()

In [25]:
#возвращает решение начального уравнения
def returner (R_1, R_2, R_3):
    X = R_1[0]
    T = R_1[1]
    R_1 = 1/4*np.array(R_1[2])
    R_2 = 1/4*np.array(R_2[2])
    R_3 = 1/4*np.array(R_3[2])
    return (X, T, 
            -R_1 - R_2 + 2*R_3, 
           R_1 + 2*R_2 - R_3,
           2*R_1 + R_2 - R_3)

In [26]:
#Возвращает разность двух решений
def differ (f1, f2, n, Tn, Xm):
    Rd = np.array(f1(Tn, Xm, A[n], R_th[n])[2]) - np.array(f2(Tn, Xm, n)[2])
    T = np.linspace(0, 1, Tn)
    X = np.linspace(0, 1, Xm)
    return (X, T, Rd)

In [86]:
#решение при помощи схемы Лакса-Вендроффа
def LV (N, Tn, Xm):
    R = np.zeros((Tn, Xm))
    X = np.linspace(0, 1, Xm)
    T = np.linspace(0, 1, Tn)
    tau = T[1] - T[0]
    h = X[1] - X[0]
    R[:, Xm-1] = R_th[N](1 - A[N]*T)
    R[Tn-1, :] = R_th[N](X - A[N])
    for m in range(Xm - 2, 0, -1):
        for n in range (Tn-1):
            R[n+1][m] = (1 - (A[N]*tau/h)**2)*R[n][m] + ((A[N]*tau/h)**2 + A[N]*tau/h)*(R[n][m+1] + R[n][m-1])/2
    return (X, T, R)

In [72]:
merging_ploter(corner(1000, 100, A[1], R0_2) , R_prec(100, 100, 1), title = 'Наложение решений. Синее - точное решение, Красное - метод бегущего счета')

In [73]:
ploter(differ (corner, R_prec, 1, 1000, 100), 'График разности решений')

In [74]:
#Решение начального уравнения по первой координате 
ploter (returner(plaksa (1000, 100, A[0], R_th[0]), corner (1000, 100, A[1], R_th[1]), plaksa (1000, 100, A[2], R_th[2])), 'График решения начального уравнения по первой координате')

In [75]:
def poryadok (R, R_pr, Tn = 1000):
    dif = []
    xs = []
    for i in np.linspace(100, 1000, 10):
        Xm = int(i)
        R1 = R(Tn, Xm, A[0], R0_1)
        R2 = R(Tn, Xm, A[1], R0_2)
        R3 = R(Tn, Xm, A[2], R0_3)
        dif.append(np.log(np.amax(abs(np.array(returner(R1, R2, R3)[2]) - np.array(returner(R_pr(Tn, Xm, 0), R_pr(Tn, Xm, 1), R_pr(Tn, Xm, 2))[2])))))
    xs = np.log(1/np.linspace(100, 1000, 10))
    return (dif, xs)

In [76]:
[dif, xs] = poryadok(corner, R_prec)

In [77]:
ploter(R_prec(1000, 100, 1), 'xx')

In [79]:
ploter(R_prec(100, 100, 1), 'xx')

# Найдем апостериронрный порядок аппроксимации 
Найдем его из уравнения:
$$
ln ||u_{calc} - u_{th}||(h) < p \cdot ln(h) + ln(c)
$$
Для этого построим графика логарифма максимума невязки от логарифма шага

In [80]:
fig = px.scatter(x=xs, y=dif, trendline="ols")
fig.show()
results = px.get_trendline_results(fig)
print(results.px_fit_results.iloc[0].summary())

                            OLS Regression Results                            
Dep. Variable:                      y   R-squared:                       0.972
Model:                            OLS   Adj. R-squared:                  0.968
Method:                 Least Squares   F-statistic:                     276.9
Date:                Fri, 14 May 2021   Prob (F-statistic):           1.72e-07
Time:                        20:54:24   Log-Likelihood:                 14.353
No. Observations:                  10   AIC:                            -24.71
Df Residuals:                       8   BIC:                            -24.10
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const         -0.1329      0.180     -0.737      0.4

/usr/local/lib/python3.7/dist-packages/scipy/stats/stats.py:1535: UserWarning:

kurtosistest only valid for n>=20 ... continuing anyway, n=10



Таким образом, апостериорный порядок аппроксимации: 0.5

In [81]:
def differ (f1, f2, n, Tn, Xm):
    Rd = np.array(f1(Tn, Xm, A[n], R_th[n])[2]) - np.array(f2(Tn, Xm, n)[2])
    T = np.linspace(0, 1, Tn)
    X = np.linspace(0, 1, Xm)
    return (X, T, Rd)

In [87]:
ploter(LV(0, 100, 100), 'метод Лакса-Вендроффа')  

In [88]:
N = 1
Tn = 6
Xm = 6
R = np.zeros((Tn, Xm))
X = np.linspace(0, 1, Xm)
T = np.linspace(0, 1, Tn)
tau = T[1] - T[0]
h = X[1] - X[0]
R[:, Xm-1] = [1 for i in range(Xm)]
R[Tn-1, :] = [2 for i in range(Tn)]
for m in range(Xm - 2, -1, -1):
    for n in range (Tn-2, -1, -1):
        R[n][m] = (-1)*R[n+1][m+1] - (1 - h/(2*tau*A[N]))/(1+h/(2*tau*A[N]))*(R[n][m+1] - R[n+1][m])
    print (R)
    break

[[ 0.       0.       0.       0.      -3.66304  1.     ]
 [ 0.       0.       0.       0.      -3.4384   1.     ]
 [ 0.       0.       0.       0.      -3.064    1.     ]
 [ 0.       0.       0.       0.      -2.44     1.     ]
 [ 0.       0.       0.       0.      -1.4      1.     ]
 [ 2.       2.       2.       2.       2.       2.     ]]
